In [1]:
import pandas as pd
import numpy as np
import datetime as dt
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import train_test_split, cross_val_score, TimeSeriesSplit
import plotly.express as px

**Carga de Archivo y primer vistaso** 

El dataset esta compuesto por una variable de tiempo, la inversion en diferentes medios, y las ventas por fecha en dias. 

In [2]:
data = pd.read_csv('./Data/mmm.csv')
data

Date        TV    Radio  Banners     Sales
0    2018-01-07  13528.10     0.00     0.00   9779.80
1    2018-01-14      0.00  5349.65  2218.93  13245.19
2    2018-01-21      0.00  4235.86  2046.96  12022.66
3    2018-01-28      0.00  3562.21     0.00   8846.95
4    2018-02-04      0.00     0.00  2187.29   9797.07
..          ...       ...      ...      ...       ...
195  2021-10-03      0.00     0.00  1691.68   9030.17
196  2021-10-10  11543.58  4615.35  2518.88  15904.11
197  2021-10-17      0.00  4556.16  1919.19  12839.29
198  2021-10-24      0.00     0.00  1707.65   9063.45
199  2021-10-31      0.00     0.00  1863.31   7250.21

[200 rows x 5 columns]

## EDA

No tenemos datos nulos en el dataset.
Cuenta con 5 variables/features:
- 1: tiempo "Date"
- 2: inversion "TV" 
- 3: inversion "Radio"
- 4: inversion "Banners"
- 5: ventas "Sales"

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 200 entries, 0 to 199
Data columns (total 5 columns):
 #   Column   Non-Null Count  Dtype  
---  ------   --------------  -----  
 0   Date     200 non-null    object 
 1   TV       200 non-null    float64
 2   Radio    200 non-null    float64
 3   Banners  200 non-null    float64
 4   Sales    200 non-null    float64
dtypes: float64(4), object(1)
memory usage: 7.9+ KB


Se puede ver que no tenemos inversion para: 

- tv en mas del 50% de las semanas
- Radio en mas del 50% de las semanas
- Banner tenemos inversion apartir del 25% de las semanas


In [4]:
(data.describe().T).to_csv('describe.csv',sep='|')

In [5]:
data.describe().T

count         mean          std      min        25%        50%  \
TV       200.0   2946.20765  4749.646908     0.00     0.0000      0.000   
Radio    200.0   2213.58505  2505.967886     0.00     0.0000      0.000   
Banners  200.0   1520.72255   870.764354     0.00  1657.1950   1918.990   
Sales    200.0  10668.14150  2700.706683  4532.33  8396.9425  10853.105   

                75%       max  
TV        7938.5275  13901.55  
Radio     4624.0275   7696.22  
Banners   2069.7675   2518.88  
Sales    12566.9950  17668.34

In [6]:
col_medios = ['TV', 'Radio', 'Banners']
data_melt = pd.melt(data, id_vars=['Date'], value_vars=col_medios, var_name='Medio', value_name='Inversion')

In [7]:
data_melt.head()

Date Medio  Inversion
0  2018-01-07    TV    13528.1
1  2018-01-14    TV        0.0
2  2018-01-21    TV        0.0
3  2018-01-28    TV        0.0
4  2018-02-04    TV        0.0

la inversion en tv es mas alto que radio y a su vez este es mas alto que el de banner

In [8]:
fig = px.pie(data_melt, 
            values='Inversion', 
            names='Medio',
            title='Share of Investment by Media')
fig.show()

Los Banners son los que estan activos

In [9]:
data2 = data.copy()
data2[['TV_%', 'Radio_%', 'Banners_%']] = data2[['TV', 'Radio', 'Banners']].apply(lambda x: x / x.sum(), axis=1)
px.bar(data2, x="Date", y=['TV_%', 'Radio_%', 'Banners_%'], title='Share of Investment by Media')

Las Ventas correlacionan con las inveriones en los medios

In [10]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Bar(x=data['Date'], y=data['TV'], name='TV'), secondary_y=False)
fig.add_trace(go.Bar(x=data['Date'], y=data['Radio'], name='Radio'), secondary_y=False)
fig.add_trace(go.Bar(x=data['Date'], y=data['Banners'], name='Banners'), secondary_y=False)
fig.add_trace(go.Scatter(x=data['Date'], y=data['Sales'], name='Sales'), secondary_y=True)

fig.show()

In [75]:
import plotly.figure_factory as ff

df = data.corr().round(2)

fig = ff.create_annotated_heatmap(df.values.tolist(),
                                  x=df.columns.values.tolist(),
                                  y=df.index.values.tolist(),
                                 colorscale='Viridis')
fig.update_layout(title_text='Correlacion')
fig['data'][0]['showscale'] = True
fig.show()

## Creacion del Modelo

### Preparacion y Divicion de Datos

In [44]:
data = data.set_index('Date')
data

TV    Radio  Banners     Sales
Date                                            
2018-01-07  13528.10     0.00     0.00   9779.80
2018-01-14      0.00  5349.65  2218.93  13245.19
2018-01-21      0.00  4235.86  2046.96  12022.66
2018-01-28      0.00  3562.21     0.00   8846.95
2018-02-04      0.00     0.00  2187.29   9797.07
...              ...      ...      ...       ...
2021-10-03      0.00     0.00  1691.68   9030.17
2021-10-10  11543.58  4615.35  2518.88  15904.11
2021-10-17      0.00  4556.16  1919.19  12839.29
2021-10-24      0.00     0.00  1707.65   9063.45
2021-10-31      0.00     0.00  1863.31   7250.21

[200 rows x 4 columns]

In [45]:
matrix_data = data[['TV','Radio','Banners','Sales']]
matrix_data.sample(3)

TV    Radio  Banners     Sales
Date                                       
2021-06-06  0.0  5936.74  2265.29  10581.72
2019-11-10  0.0     0.00  1915.07   8018.56
2018-09-30  0.0     0.00  1764.47   8036.91

In [13]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(matrix_data, test_size=0.2, random_state=123)

distributions= np.array([len(train), len(test)])
print(distributions)

[160  40]


### Creacion de Efecto de Saturacion

Queremos crear una transformación (= función matemática) con las siguientes propiedades:
- Si los gastos son 0, los gastos saturados también son 0.
- La transformación aumenta la saturacion del canal de inversion, es decir, cuanto mayor es el gasto en inversion, mayor es la saturacion.
- Los valores saturados no crecen hasta el infinito están delimitados en la parte superior por 1

In [14]:
from scipy.signal import convolve2d
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.utils.validation import check_is_fitted, check_array

class ExponentialSaturation (BaseEstimator, TransformerMixin):
    def __init__ (self, a = 1.):
        self.a = a
        
    def fit(self, X, y = None):
        X = check_array(X) 
        self._check_n_features(X, reset = True)
        return self
    
    def transform (self, X):
        check_is_fitted (self)
        X = check_array (X)
        self._check_n_features (X, reset = False)
        return 1 - np.exp (-self.a * X)

### Creacion del Efecto de Arrastre (CarryOver)

Con esto se puede modelar el impacto de la inversion en semanas siguientes a la inversion
mediante un efecto de degradacion semana con semana

In [15]:
from sklearn.base import BaseEstimator, TransformerMixin

class ExponentialCarryover(BaseEstimator, TransformerMixin): 
    def __init__(self, strength = 0.5, length = 1):
        self.strength = strength
        self.length = length
        
    def fit(self, X, y = None):
        X = check_array(X)
        self._check_n_features(X, reset=True)
        self.sliding_window_ = (
            self.strength ** np.arange(self.length + 1)
        ).reshape(-1, 1)
        return self

    def transform(self, X: np.ndarray):
        check_is_fitted(self)
        X = check_array(X)
        self._check_n_features(X, reset=False)
        convolution = convolve2d(X, self.sliding_window_)
        if self.length > 0:
            convolution = convolution[: -self.length]
        return convolution 

### Definicion del PipeLine de Datos

In [16]:
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LinearRegression

Aqui se aplica a cada variable la tranformacion individual y no una sola tranformacion a todas las variables

In [17]:
adstock = ColumnTransformer([
        ('tv_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['TV']),
        ('radio_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Radio']),
        ('banners_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Banners'])
])

model = Pipeline([
    ('adstock', adstock),
    ('regression', LinearRegression())
])

#### Diagrama de nuestro PipeLine

In [18]:
from sklearn import set_config

set_config(display="diagram")
model

Pipeline(steps=[('adstock',
                 ColumnTransformer(transformers=[('tv_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['TV']),
                                                 ('radio_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Radio']),
                                                 ('banners_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Banners'])])),
                ('regression', LinearRegression())])

In [19]:
X_train = train.drop(columns='Sales')
Y_train = train['Sales']

Entrenando el modelo

In [20]:
model.fit(X_train,Y_train)

Pipeline(steps=[('adstock',
                 ColumnTransformer(transformers=[('tv_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['TV']),
                                                 ('radio_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Radio']),
                                                 ('banners_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Banners'])])),
                ('regression', LinearRegression())])

In [21]:
from sklearn.model_selection import cross_val_score, TimeSeriesSplit

x = matrix_data.drop(columns='Sales')
y = matrix_data['Sales']

print(cross_val_score(model, x, y, cv=TimeSeriesSplit()).mean())

0.552719007323667


Aqui el modelo con los valores establecidos de fueza y longitud da una validacion muy baja pero con la siguiente herramienta se buscaran los mejores valores para obtener un mejor cross

### Optuna
Nos permite encontrar los mejores parametros para las variables como fueza, longitud etc

Entonces Optuna es una biblioteca avanzada para tareas de optimización. Entre muchas otras cosas, ofrece una clase compatible con scikit-learn OptunaSearchCVque puede ver como un reemplazo directo de scikit-learn GridSearchCVy RandomizedSearchCV.
En pocas palabras, OptunaSearchCVes una versión mucho más inteligente de RandomizedSearchCV. Mientras RandomizedSearchCVcamina aleatoriamente solo, OptunaSearchCVcamina aleatoriamente al principio, pero luego verifica las combinaciones de hiperparámetros que parecen más prometedoras.


In [22]:
from optuna.integration import OptunaSearchCV
from optuna.distributions import UniformDistribution, IntUniformDistribution

Le dices a Optuna que optimice model. Lo hace mediante el uso de todos los parámetros que especifique en param_distributions. Debido a que nuestro modelo está bastante anidado, es decir, hay tuberías en un transformador de columna que también está en una tubería, tenemos que especificar exactamente qué hiperparámetro queremos ajustar. Esto se hace a través de cadenas como adstock__tv_pipe__carryover__strength, donde dos guiones bajos separan diferentes niveles del modelo completo. Encontrará las palabras adstock, tv_pipe, carryovertodo en la especificación del modelo, mientras que strengthes un parámetro del ExponentialCarryovertransformador.

In [23]:
tuned_model = OptunaSearchCV(
    estimator=model,
    param_distributions={
        'adstock__tv_pipe__carryover__strength':UniformDistribution(0, 1),  #Probara con valores de 0, 1
        'adstock__tv_pipe__carryover__length':IntUniformDistribution(0, 6), #Probara con valores de 0, 6
        'adstock__tv_pipe__saturation__a': UniformDistribution(0,0.01),     #Probara con valores de 0, 0.01
        'adstock__radio_pipe__carryover__strength':UniformDistribution(0, 1),
        'adstock__radio_pipe__carryover__length':IntUniformDistribution(0, 6),
        'adstock__radio_pipe__saturation__a': UniformDistribution(0,0.01),
        'adstock__banners_pipe__carryover__strength':UniformDistribution(0, 1),
        'adstock__banners_pipe__carryover__length':IntUniformDistribution(0, 6),
        'adstock__banners_pipe__saturation__a':UniformDistribution(0, 0.01),
    },
    n_trials=1000,
    cv=TimeSeriesSplit(),
    random_state=0
)

/tmp/ipykernel_5541/1057903697.py:1: ExperimentalWarning:

OptunaSearchCV is experimental (supported from v0.17.0). The interface can change in the future.



##### Comprobación de rendimiento
Verifiquemos el rendimiento usando este modelo optimizado llamado tuned_model

In [24]:
cross_val_score (tuned_model, x, y, cv = TimeSeriesSplit ())

/home/dsandovalflavio/anaconda3/envs/ProyectMMM/lib/python3.9/site-packages/sklearn/base.py:82: ExperimentalWarning:

OptunaSearchCV is experimental (supported from v0.17.0). The interface can change in the future.

[I 2022-01-12 10:09:35,386] A new study created in memory with name: no-name-fc92bbf0-07a6-41fb-8a1a-8d51a3ad9d60
[I 2022-01-12 10:09:35,604] Trial 0 finished with value: -347726.57392333506 and parameters: {'adstock__tv_pipe__carryover__strength': 0.4860473230215504, 'adstock__tv_pipe__carryover__length': 4, 'adstock__tv_pipe__saturation__a': 0.009855760506615989, 'adstock__radio_pipe__carryover__strength': 0.1955964101622225, 'adstock__radio_pipe__carryover__length': 4, 'adstock__radio_pipe__saturation__a': 0.00980582177099305, 'adstock__banners_pipe__carryover__strength': 0.18048029738995275, 'adstock__banners_pipe__carryover__length': 4, 'adstock__banners_pipe__saturation__a': 0.008463095456331128}. Best is trial 0 with value: -347726.57392333506.
[I 2022-01-12 10:09:35

[I 2022-01-12 10:09:38,546] Trial 12 finished with value: 0.42591029001181174 and parameters: {'adstock__tv_pipe__carryover__strength': 0.03169671055224428, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.007125437423360974, 'adstock__radio_pipe__carryover__strength': 0.6373300134363695, 'adstock__radio_pipe__carryover__length': 0, 'adstock__radio_pipe__saturation__a': 0.004711808975008528, 'adstock__banners_pipe__carryover__strength': 0.46928350526534973, 'adstock__banners_pipe__carryover__length': 3, 'adstock__banners_pipe__saturation__a': 8.111975505019578e-05}. Best is trial 10 with value: 0.4347928943151992.
[I 2022-01-12 10:09:38,863] Trial 13 finished with value: -0.17565104907136228 and parameters: {'adstock__tv_pipe__carryover__strength': 0.033173661507125786, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.007499720250088893, 'adstock__radio_pipe__carryover__strength': 0.5154746235126143, 'adstock__radio_pipe__carr

[I 2022-01-12 10:09:43,165] Trial 25 finished with value: -0.2262191663435344 and parameters: {'adstock__tv_pipe__carryover__strength': 0.3789302619088629, 'adstock__tv_pipe__carryover__length': 2, 'adstock__tv_pipe__saturation__a': 0.008798311543210369, 'adstock__radio_pipe__carryover__strength': 0.7405502472543892, 'adstock__radio_pipe__carryover__length': 1, 'adstock__radio_pipe__saturation__a': 0.004069152167198089, 'adstock__banners_pipe__carryover__strength': 0.13842120353677467, 'adstock__banners_pipe__carryover__length': 4, 'adstock__banners_pipe__saturation__a': 0.0017495770979039872}. Best is trial 21 with value: 0.4891510425152353.
[I 2022-01-12 10:09:43,409] Trial 26 finished with value: -41.78006285835949 and parameters: {'adstock__tv_pipe__carryover__strength': 0.23247647103303992, 'adstock__tv_pipe__carryover__length': 1, 'adstock__tv_pipe__saturation__a': 0.005907603737703634, 'adstock__radio_pipe__carryover__strength': 0.3441909196398199, 'adstock__radio_pipe__carryove

[I 2022-01-12 10:09:47,737] Trial 38 finished with value: -0.41706645220941196 and parameters: {'adstock__tv_pipe__carryover__strength': 0.13574858821221272, 'adstock__tv_pipe__carryover__length': 2, 'adstock__tv_pipe__saturation__a': 0.00853139251254127, 'adstock__radio_pipe__carryover__strength': 0.12207597632961228, 'adstock__radio_pipe__carryover__length': 2, 'adstock__radio_pipe__saturation__a': 0.008847923407673602, 'adstock__banners_pipe__carryover__strength': 0.14584863904139012, 'adstock__banners_pipe__carryover__length': 1, 'adstock__banners_pipe__saturation__a': 0.005923410208733965}. Best is trial 35 with value: 0.5972436914471184.
[I 2022-01-12 10:09:48,184] Trial 39 finished with value: -1.1349982049247966 and parameters: {'adstock__tv_pipe__carryover__strength': 0.2022878337335403, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.009906815639190597, 'adstock__radio_pipe__carryover__strength': 0.06164939101657957, 'adstock__radio_pipe__carryo

[I 2022-01-12 10:09:51,944] Trial 51 finished with value: 0.5880744614694947 and parameters: {'adstock__tv_pipe__carryover__strength': 0.6684421481036108, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.002861524338100032, 'adstock__radio_pipe__carryover__strength': 0.06733295397155058, 'adstock__radio_pipe__carryover__length': 6, 'adstock__radio_pipe__saturation__a': 0.009944816805693672, 'adstock__banners_pipe__carryover__strength': 0.014869341945969089, 'adstock__banners_pipe__carryover__length': 0, 'adstock__banners_pipe__saturation__a': 0.004077443246542196}. Best is trial 41 with value: 0.6001180331087309.
[I 2022-01-12 10:09:52,190] Trial 52 finished with value: 0.5926780964743946 and parameters: {'adstock__tv_pipe__carryover__strength': 0.712772355874009, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.00041059457691931095, 'adstock__radio_pipe__carryover__strength': 0.10166625388886072, 'adstock__radio_pipe__carryov

...

[I 2022-01-12 10:38:39,382] Trial 948 finished with value: 0.5344731528905754 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5134832074240906, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.0005628753761375734, 'adstock__radio_pipe__carryover__strength': 0.06646684120054103, 'adstock__radio_pipe__carryover__length': 3, 'adstock__radio_pipe__saturation__a': 0.004106549998748102, 'adstock__banners_pipe__carryover__strength': 0.02873109562499128, 'adstock__banners_pipe__carryover__length': 5, 'adstock__banners_pipe__saturation__a': 0.001285452708213232}. Best is trial 466 with value: 0.9265224700643925.
[I 2022-01-12 10:38:39,941] Trial 949 finished with value: 0.7569862210483513 and parameters: {'adstock__tv_pipe__carryover__strength': 0.48652772939406763, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.00035116218105837546, 'adstock__radio_pipe__carryover__strength': 0.04888685824070945, 'adstock__radio_pipe__ca

[I 2022-01-12 10:38:50,821] Trial 961 finished with value: 0.8193786802260103 and parameters: {'adstock__tv_pipe__carryover__strength': 0.52435345221639, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.00016770416634238422, 'adstock__radio_pipe__carryover__strength': 0.055066668279519296, 'adstock__radio_pipe__carryover__length': 3, 'adstock__radio_pipe__saturation__a': 0.004360388088286323, 'adstock__banners_pipe__carryover__strength': 0.02902734074994394, 'adstock__banners_pipe__carryover__length': 5, 'adstock__banners_pipe__saturation__a': 0.0018123070432554903}. Best is trial 466 with value: 0.9265224700643925.
[I 2022-01-12 10:38:51,272] Trial 962 finished with value: -232.90250840655412 and parameters: {'adstock__tv_pipe__carryover__strength': 0.4930700292407851, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.007445720458182668, 'adstock__radio_pipe__carryover__strength': 0.0002149351923386375, 'adstock__radio_pipe__c

[I 2022-01-12 10:38:59,542] Trial 974 finished with value: 0.7355829327822948 and parameters: {'adstock__tv_pipe__carryover__strength': 0.47773199864040494, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.00045754378353471593, 'adstock__radio_pipe__carryover__strength': 9.42946453815391e-06, 'adstock__radio_pipe__carryover__length': 3, 'adstock__radio_pipe__saturation__a': 0.00442160147959938, 'adstock__banners_pipe__carryover__strength': 0.08807085733746342, 'adstock__banners_pipe__carryover__length': 5, 'adstock__banners_pipe__saturation__a': 0.003042460513128239}. Best is trial 466 with value: 0.9265224700643925.
[I 2022-01-12 10:38:59,994] Trial 975 finished with value: 0.9178373771235314 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5246459191168981, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 6.753441248116217e-06, 'adstock__radio_pipe__carryover__strength': 0.020364222019823578, 'adstock__radio_pipe__c

[I 2022-01-12 10:39:06,079] Trial 987 finished with value: 0.5445094069085596 and parameters: {'adstock__tv_pipe__carryover__strength': 0.529625623939341, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.00034460338965806137, 'adstock__radio_pipe__carryover__strength': 5.4941339657902717e-05, 'adstock__radio_pipe__carryover__length': 3, 'adstock__radio_pipe__saturation__a': 0.003986016251915348, 'adstock__banners_pipe__carryover__strength': 0.6892658468728922, 'adstock__banners_pipe__carryover__length': 3, 'adstock__banners_pipe__saturation__a': 0.0019920799732923156}. Best is trial 466 with value: 0.9265224700643925.
[I 2022-01-12 10:39:07,174] Trial 988 finished with value: 0.8707111353420511 and parameters: {'adstock__tv_pipe__carryover__strength': 0.4681538242174626, 'adstock__tv_pipe__carryover__length': 5, 'adstock__tv_pipe__saturation__a': 0.00018040246522943522, 'adstock__radio_pipe__carryover__strength': 0.03854468876955435, 'adstock__radio_pipe__

array([0.84735301, 0.92050716, 0.70872965, 0.94380527, 0.90815941])

El r² medio validado de forma cruzada es 0,87, lo que representa una gran mejora en comparación con el modelo no optimizado (0,55)

In [25]:
tuned_model.fit(x,y)

[I 2022-01-12 10:39:14,886] A new study created in memory with name: no-name-d4a4cf8a-70d7-4e41-9db7-f49de355baa8
[I 2022-01-12 10:39:15,757] Trial 0 finished with value: 0.1377916398119512 and parameters: {'adstock__tv_pipe__carryover__strength': 0.4860473230215504, 'adstock__tv_pipe__carryover__length': 4, 'adstock__tv_pipe__saturation__a': 0.009855760506615989, 'adstock__radio_pipe__carryover__strength': 0.1955964101622225, 'adstock__radio_pipe__carryover__length': 4, 'adstock__radio_pipe__saturation__a': 0.00980582177099305, 'adstock__banners_pipe__carryover__strength': 0.18048029738995275, 'adstock__banners_pipe__carryover__length': 4, 'adstock__banners_pipe__saturation__a': 0.008463095456331128}. Best is trial 0 with value: 0.1377916398119512.
[I 2022-01-12 10:39:16,321] Trial 1 finished with value: -7.206841484775086e+17 and parameters: {'adstock__tv_pipe__carryover__strength': 0.7967092952533198, 'adstock__tv_pipe__carryover__length': 6, 'adstock__tv_pipe__saturation__a': 0.005

[I 2022-01-12 10:39:21,128] Trial 13 finished with value: 0.5294254293595315 and parameters: {'adstock__tv_pipe__carryover__strength': 0.03484838613823089, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.007515109949576203, 'adstock__radio_pipe__carryover__strength': 0.06434091848136951, 'adstock__radio_pipe__carryover__length': 5, 'adstock__radio_pipe__saturation__a': 0.004169507569226943, 'adstock__banners_pipe__carryover__strength': 0.9992866967535542, 'adstock__banners_pipe__carryover__length': 4, 'adstock__banners_pipe__saturation__a': 0.0035172201615055474}. Best is trial 11 with value: 0.5759188916436802.
[I 2022-01-12 10:39:21,813] Trial 14 finished with value: 0.6419576763129411 and parameters: {'adstock__tv_pipe__carryover__strength': 0.1293727365984736, 'adstock__tv_pipe__carryover__length': 1, 'adstock__tv_pipe__saturation__a': 0.007942340920804446, 'adstock__radio_pipe__carryover__strength': 0.3760710906749566, 'adstock__radio_pipe__carryover

[I 2022-01-12 10:39:27,029] Trial 26 finished with value: 0.5401489721742486 and parameters: {'adstock__tv_pipe__carryover__strength': 0.9568918478478259, 'adstock__tv_pipe__carryover__length': 1, 'adstock__tv_pipe__saturation__a': 0.007717148185238824, 'adstock__radio_pipe__carryover__strength': 0.7292940211579039, 'adstock__radio_pipe__carryover__length': 1, 'adstock__radio_pipe__saturation__a': 0.0021624836510699265, 'adstock__banners_pipe__carryover__strength': 0.7396951876502812, 'adstock__banners_pipe__carryover__length': 2, 'adstock__banners_pipe__saturation__a': 0.005494992206342406}. Best is trial 17 with value: 0.6674883324700228.
[I 2022-01-12 10:39:27,670] Trial 27 finished with value: 0.5623904746185099 and parameters: {'adstock__tv_pipe__carryover__strength': 0.20586925156508742, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.006532169033180348, 'adstock__radio_pipe__carryover__strength': 0.984650917089326, 'adstock__radio_pipe__carryover__

[I 2022-01-12 10:39:32,655] Trial 39 finished with value: 0.5727253625866734 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5163282036570265, 'adstock__tv_pipe__carryover__length': 2, 'adstock__tv_pipe__saturation__a': 0.006046007334627433, 'adstock__radio_pipe__carryover__strength': 0.22603650296327227, 'adstock__radio_pipe__carryover__length': 3, 'adstock__radio_pipe__saturation__a': 0.001399587681176526, 'adstock__banners_pipe__carryover__strength': 0.12037987128756994, 'adstock__banners_pipe__carryover__length': 2, 'adstock__banners_pipe__saturation__a': 0.003548825977555077}. Best is trial 35 with value: 0.6820541950277947.
[I 2022-01-12 10:39:33,014] Trial 40 finished with value: 0.3683981174646022 and parameters: {'adstock__tv_pipe__carryover__strength': 0.404297331870517, 'adstock__tv_pipe__carryover__length': 3, 'adstock__tv_pipe__saturation__a': 0.0028153766017436446, 'adstock__radio_pipe__carryover__strength': 0.3152712159346233, 'adstock__radio_pipe__carryover_

[I 2022-01-12 10:39:36,830] Trial 52 finished with value: 0.7965821934224125 and parameters: {'adstock__tv_pipe__carryover__strength': 0.6908103049726186, 'adstock__tv_pipe__carryover__length': 1, 'adstock__tv_pipe__saturation__a': 0.0032018228837864416, 'adstock__radio_pipe__carryover__strength': 0.11980445202269874, 'adstock__radio_pipe__carryover__length': 1, 'adstock__radio_pipe__saturation__a': 0.0004932803916013334, 'adstock__banners_pipe__carryover__strength': 0.11583703032521153, 'adstock__banners_pipe__carryover__length': 0, 'adstock__banners_pipe__saturation__a': 0.006329060557662189}. Best is trial 52 with value: 0.7965821934224125.
[I 2022-01-12 10:39:37,143] Trial 53 finished with value: 0.7010939590430525 and parameters: {'adstock__tv_pipe__carryover__strength': 0.7086369589674, 'adstock__tv_pipe__carryover__length': 0, 'adstock__tv_pipe__saturation__a': 0.0035067876310144654, 'adstock__radio_pipe__carryover__strength': 0.1315381943569255, 'adstock__radio_pipe__carryover_

...

[I 2022-01-12 10:46:10,527] Trial 949 finished with value: 0.8900310834542348 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5024545934463468, 'adstock__tv_pipe__carryover__length': 4, 'adstock__tv_pipe__saturation__a': 0.0001817134992983514, 'adstock__radio_pipe__carryover__strength': 0.4405186760006912, 'adstock__radio_pipe__carryover__length': 0, 'adstock__radio_pipe__saturation__a': 0.00019798357255797243, 'adstock__banners_pipe__carryover__strength': 0.3128397068861912, 'adstock__banners_pipe__carryover__length': 0, 'adstock__banners_pipe__saturation__a': 0.00682915115135178}. Best is trial 910 with value: 0.9340874940105468.
[I 2022-01-12 10:46:10,833] Trial 950 finished with value: 0.9273045424448785 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5754886949341707, 'adstock__tv_pipe__carryover__length': 3, 'adstock__tv_pipe__saturation__a': 9.92883851829746e-07, 'adstock__radio_pipe__carryover__strength': 0.4716400836527849, 'adstock__radio_pipe__carryov

[I 2022-01-12 10:46:15,174] Trial 962 finished with value: 0.7701313543558639 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5702220124394719, 'adstock__tv_pipe__carryover__length': 3, 'adstock__tv_pipe__saturation__a': 0.00031950507391555427, 'adstock__radio_pipe__carryover__strength': 0.4673059631673803, 'adstock__radio_pipe__carryover__length': 0, 'adstock__radio_pipe__saturation__a': 0.000605938436062652, 'adstock__banners_pipe__carryover__strength': 0.30664271394751236, 'adstock__banners_pipe__carryover__length': 0, 'adstock__banners_pipe__saturation__a': 0.006139551443400663}. Best is trial 910 with value: 0.9340874940105468.
[I 2022-01-12 10:46:15,552] Trial 963 finished with value: 0.5845219144271729 and parameters: {'adstock__tv_pipe__carryover__strength': 0.573400955025708, 'adstock__tv_pipe__carryover__length': 3, 'adstock__tv_pipe__saturation__a': 0.008411260038136685, 'adstock__radio_pipe__carryover__strength': 0.47650865839215295, 'adstock__radio_pipe__carryo

[I 2022-01-12 10:46:20,807] Trial 975 finished with value: 0.46839882047672876 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5994373612485513, 'adstock__tv_pipe__carryover__length': 4, 'adstock__tv_pipe__saturation__a': 0.002192015319013758, 'adstock__radio_pipe__carryover__strength': 0.4211336970845768, 'adstock__radio_pipe__carryover__length': 0, 'adstock__radio_pipe__saturation__a': 0.0005641231280514508, 'adstock__banners_pipe__carryover__strength': 0.2486199287631979, 'adstock__banners_pipe__carryover__length': 0, 'adstock__banners_pipe__saturation__a': 0.0071714631176273995}. Best is trial 910 with value: 0.9340874940105468.
[I 2022-01-12 10:46:21,359] Trial 976 finished with value: 0.5585040928247647 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5458317546953954, 'adstock__tv_pipe__carryover__length': 4, 'adstock__tv_pipe__saturation__a': 0.0007659598279302893, 'adstock__radio_pipe__carryover__strength': 0.397148592624309, 'adstock__radio_pipe__carryo

[I 2022-01-12 10:46:28,233] Trial 988 finished with value: 0.8750771549016217 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5643778943344775, 'adstock__tv_pipe__carryover__length': 3, 'adstock__tv_pipe__saturation__a': 0.00017929546869005128, 'adstock__radio_pipe__carryover__strength': 0.48251338573407615, 'adstock__radio_pipe__carryover__length': 1, 'adstock__radio_pipe__saturation__a': 2.8809427206614503e-06, 'adstock__banners_pipe__carryover__strength': 0.30192134564698037, 'adstock__banners_pipe__carryover__length': 0, 'adstock__banners_pipe__saturation__a': 0.0069874453621672486}. Best is trial 910 with value: 0.9340874940105468.
[I 2022-01-12 10:46:29,183] Trial 989 finished with value: 0.7468418008543818 and parameters: {'adstock__tv_pipe__carryover__strength': 0.5596334256392299, 'adstock__tv_pipe__carryover__length': 3, 'adstock__tv_pipe__saturation__a': 0.00040130868391883727, 'adstock__radio_pipe__carryover__strength': 0.46710736223084126, 'adstock__radio_pipe_

OptunaSearchCV(cv=TimeSeriesSplit(gap=0, max_train_size=None, n_splits=5, test_size=None),
               estimator=Pipeline(steps=[('adstock',
                                          ColumnTransformer(transformers=[('tv_pipe',
                                                                           Pipeline(steps=[('carryover',
                                                                                            ExponentialCarryover()),
                                                                                           ('saturation',
                                                                                            ExponentialSaturation())]),
                                                                           ['TV']),
                                                                          ('radio_pipe',
                                                                           Pipeline(steps=[('carryover',
                                                                                            ExponentialCarryover()),
                                                                                           ('saturation',...
                                    'adstock__radio_pipe__carryover__strength': UniformDistribution(high=1.0, low=0.0),
                                    'adstock__radio_pipe__saturation__a': UniformDistribution(high=0.01, low=0.0),
                                    'adstock__tv_pipe__carryover__length': IntUniformDistribution(high=6, low=0, step=1),
                                    'adstock__tv_pipe__carryover__strength': UniformDistribution(high=1.0, low=0.0),
                                    'adstock__tv_pipe__saturation__a': UniformDistribution(high=0.01, low=0.0)},
               random_state=0)

Los hiperparámetros óptimos son los siguientes:

In [27]:
tuned_model.best_params_

{'adstock__tv_pipe__carryover__strength': 0.5248878517291329,
 'adstock__tv_pipe__carryover__length': 4,
 'adstock__tv_pipe__saturation__a': 1.4649722346562529e-05,
 'adstock__radio_pipe__carryover__strength': 0.45523455448406197,
 'adstock__radio_pipe__carryover__length': 0,
 'adstock__radio_pipe__saturation__a': 0.0001974038926379962,
 'adstock__banners_pipe__carryover__strength': 0.3340342963936898,
 'adstock__banners_pipe__carryover__length': 0,
 'adstock__banners_pipe__saturation__a': 0.007256873558015173}

In [28]:
print (tuned_model.best_estimator_.named_steps ['regression']. coef_)

[27926.6810003   4114.46117033  2537.18883927]


In [29]:
print (tuned_model.best_estimator_.named_steps ['regression'].intercept_)

5348.966158957057


In [46]:
matrix_data[['TV_sat','Radio_sat','Banners_sat']] = tuned_model.best_estimator_.named_steps['adstock'].transform(x)

In [77]:
matrix_data.head(3)

TV    Radio  Banners     Sales    TV_sat  Radio_sat  \
Date                                                                   
2018-01-07  13528.1     0.00     0.00   9779.80  0.179780   0.000000   
2018-01-14      0.0  5349.65  2218.93  13245.19  0.098796   0.652170   
2018-01-21      0.0  4235.86  2046.96  12022.66  0.053137   0.566635   

            Banners_sat  
Date                     
2018-01-07          0.0  
2018-01-14          1.0  
2018-01-21          1.0

### Interpretando el Modelo



In [32]:
px.scatter(x = matrix_data['TV'], y = matrix_data['TV_sat'])

In [33]:
px.scatter(x = matrix_data['Radio'], y = matrix_data['Radio_sat'])

In [34]:
px.scatter(x = matrix_data['Banners'], y = matrix_data['Banners_sat'])

- Podemos ver que el modelo piensa que el canal de televisión todavía está bastante subsaturado: gastar más aquí podría ser beneficioso para las ventas. Tenga en cuenta que nuestro gasto máximo en televisión fue de aproximadamente 15000.
- La radio parece un poco más saturada, pero aumentar los gastos aquí todavía parece razonable. El gasto máximo en este canal fue de unos 7700.
- Los banners se ven sobresaturados . El gasto máximo aquí fue de alrededor de 2500, con un valor de función de casi 1 ya. Los gastos más altos no parecen lograr mucho.

In [61]:
date = matrix_data.reset_index()[['Date']]

In [62]:
adstock_data.mul(weights).assign(Base=base)

TV        Radio      Banners         Base
0    5020.663906     0.000000     0.000000  5348.966159
1    2759.048639  2683.328585  2537.188582  5348.966159
2    1483.939148  2331.398245  2537.187942  5348.966159
3     788.999375  2077.795974     0.000000  5348.966159
4     416.954988     0.000000  2537.188515  5348.966159
..           ...          ...          ...          ...
195  1165.913078     0.000000  2537.177014  5348.966159
196  4724.727019  2460.091906  2537.188810  5348.966159
197  2588.898671  2440.648328  2537.186570  5348.966159
198  1271.289409     0.000000  2537.178308  5348.966159
199   674.666682     0.000000  2537.185436  5348.966159

[200 rows x 4 columns]

In [63]:
adstock_data = pd.DataFrame(
    tuned_model.best_estimator_.named_steps['adstock'].transform(x),
    columns=x.columns,
    index=x.index
)
weights = pd.Series(
    tuned_model.best_estimator_.named_steps['regression'].coef_,
    index=x.columns
)
base = tuned_model.best_estimator_.named_steps['regression'].intercept_
unadj_contributions = adstock_data.mul(weights).assign(Base=base)
adj_contributions = (unadj_contributions
                     .div(unadj_contributions.sum(axis=1), axis=0)
                     .mul(y, axis=0)
                    )
adj_contributions['Date'] = date

In [78]:
adj_contributions

TV        Radio      Banners         Base        Date
0    4735.085877     0.000000     0.000000  5044.714123  2018-01-07
1    2741.796586  2666.550002  2521.323798  5315.519614  2018-01-14
2    1524.668530  2395.387668  2606.825634  5495.778168  2018-01-21
3     849.615463  2237.425840     0.000000  5759.908696  2018-01-28
4     491.976786     0.000000  2993.699288  6311.393926  2018-02-04
..           ...          ...          ...          ...         ...
195  1163.094109     0.000000  2531.042574  5336.033317  2021-10-03
196  4985.913900  2596.087855  2677.446740  5644.661505  2021-10-10
197  2573.582656  2426.209368  2522.176487  5317.321489  2021-10-17
198  1258.242009     0.000000  2511.138933  5294.069058  2021-10-24
199   571.379390     0.000000  2148.758054  4530.072556  2021-10-31

[200 rows x 5 columns]

In [65]:
inversion_melt = pd.melt(adj_contributions,
                        id_vars = 'Date',
                        value_vars = ['Base', 'Banners', 'Radio', 'TV'],
                        var_name='Medios',
                        value_name='Inversion')
inversion_melt.head()

Date Medios    Inversion
0  2018-01-07   Base  5044.714123
1  2018-01-14   Base  5315.519614
2  2018-01-21   Base  5495.778168
3  2018-01-28   Base  5759.908696
4  2018-02-04   Base  6311.393926

### Contribuciones de cada canal a las ventas

In [67]:
px.area(inversion_melt, 
        x="Date", 
        y="Inversion", 
        color="Medios")

#### Sin embargo, todavía quedan algunos cabos sueltos:
- Hemos hablado de optimizar gastos y de cómo esto no era posible con el modelo antiguo, trate nuestra tuned_modelfunción y optimícela con un programa de su elección, por ejemplo, Optuna o scipy.optimize.minimize . Agregue algunas restricciones presupuestarias a la optimización, como que la suma de los gastos debe ser inferior a 1 000 000 en total.
- Introducir datos no relacionados con el gasto en el modelo podría mejorarlo aún más. Tomemos el día de la semana , el mes , o incluso el precio del producto que queremos vender, por ejemplo. Especialmente el precio es un factor importante para las ventas: un iPhone normal ofrecido por 10000 € no generaría muchas ventas, mientras que uno por 100 € estaría agotado en un abrir y cerrar de ojos. Las características puntuales, como el mes, pueden ser interesantes para los productos de temporada, como los abanicos o el chocolate caliente. O días especiales como Navidad. ¡Reúna sus pensamientos y asegúrese de agregar todo lo que pueda influir en las ventas!